In [3]:
# Imports

import glob
import os.path as path
from scipy import misc
from scipy.io.wavfile import read
import numpy as np
import matplotlib.pyplot as plt

In [4]:
# define method for making spectogram
# modified from Ernst's spectrogram.py in Pylos github

import wave, struct
from math import *
import numpy as np
import numpy.fft as fft
import matplotlib.pyplot as plt
from scipy import signal
import sys
import pylab
import os

import datetime
import string

from bandpass_filter import *

def usage():
    print("Usage:  %s  <wav-file> <t_min (s)> <t_max (s)> \n"
          % os.path.basename(sys.argv[0]))


def get_timestamp(filename, begin_time):
    s = os.path.splitext(os.path.basename(filename))[0][10:]
    extra_minute = int(begin_time/60.)
    extra_second = int(begin_time - extra_minute*60.)
    hours = int(s[6:8])
    minutes = int(s[8:10]) + extra_minute
    seconds = int(s[10:12]) + extra_second
    if seconds > 60:
        minutes += 1
        seconds -= 60
    if minutes > 60:
        hours +=1
        minutes -= 60
        
    date = datetime.datetime(year=2000+ int(s[0:2]), month=int(s[2:4]), \
                             day=int(s[4:6]), \
                             hour = hours, minute = minutes, second = seconds)
    return date

# will have to change in order to save png of just image 
def graph_spectrogram(wav_file, begin, end, cutoff_low, cutoff_high, order, image_name):
    sound_info, Fs = get_wav_info(wav_file)
    pylab.figure(num=None, figsize=(19, 12))
    pylab.subplot(111)
    #pylab.title('spectrogram of %r' % wav_file)
    nfft = 1024 # play around with this to change width of blocks (originally it is 1024)
    data = sound_info[int(begin*Fs): int(end*Fs)]
    data = butter_bandpass_filter(data, cutoff_low, cutoff_high, Fs, order)
    plt.ylim([0, 20000])
    pylab.specgram(data, Fs=Fs, NFFT = nfft, \
                   noverlap =int(nfft * (4./5)), # play around with overlap (originally it is int(nff2/2))
                   cmap='coolwarm', \
                   mode = 'psd')
    _, _, spectrum = signal.spectrogram(data)
    plt.axis('off')
    plt.savefig(image_name, transparent = True, bbox_inches='tight', pad_inches=0) 

    #pylab.colorbar()      
    #    datestring = get_timestamp(wav_file, begin)
    #    pylab.xlabel("Time (seconds since {}) [s]".format(datestring), \
        #                 size = 16, ha ='right', x=1.0)
    #pylab.xlabel("Time (seconds)", size = 16, ha ='right', x=1.0)
    #pylab.ylabel("PSD", size = 16, ha ='right', position=(0,1))
    #pylab.show()
    plt.close()
    return spectrum
    
def get_wav_info(wav_file):
    wav = wave.open(wav_file, 'r')
    frames = wav.readframes(-1)
    sound_info = pylab.fromstring(frames, 'int16')
    frame_rate = wav.getframerate()
    wav.close()
    return sound_info, frame_rate

def make_spectrogram(filename, begin, end, image_name):
    cutoff_low = 100.
    cutoff_high = 5000.
    order = 5 
    spectrum = graph_spectrogram(filename, begin, end, cutoff_low, cutoff_high, order, image_name)
    return spectrum 

In [24]:
def make_all_spectrograms(wav_path, fn, spectrogram_folder_path):
    
    # Read in WAV File, compute stats
    full_fn = wav_path + fn
    r = read(full_fn)
    wavArr = np.array(r[1],dtype=float)
    rate = r[0]
    #plt.plot(wavArr) # test
    #plt.show() # test
    std = np.std(wavArr)
    avg = np.mean(wavArr)
    print("Average: ", avg, 
          "\nStandard Deviation: ", std, 
          "\nRate: ", rate) # test
    print(wavArr.shape)
    
    # record start of clicks

    # compute the noise by averaging measurments within one std dev of mean
    counter = 0
    noise = 0
    for i in wavArr:
        # test under here
        if (counter % 10000000 == 0):
            print(counter)
        # if value within one standard dev., use as part of noise calculation
        if (i < (avg + std) and i > (avg - std)):
            noise = noise + i
            counter = counter + 1
    noise = noise / counter
    print("Noise: ", noise)

    # threshold is 4.5 Sound-to-Noise ratio
    threshold = 4.5 * noise
    print("Threshold ", threshold)

    counter = 0
    clickStarts = []
    clickStartsSeconds = []
    first = True
    nearby = False
    nearbyCount = 0

    # looks at each instance in array representing .wav file
    for i in wavArr:

        # sees if value of instance above or below certain threshold
        if (i > threshold):
            # if no other click is nearby add to counter
            if (not nearby):
                clickStarts.append(counter)
                clickStartsSeconds.append(float(counter) / rate)
            # set nearby to true and reset nearby count
            nearby = True;
            nearbyCount = 0

        # if it has been .02 seconds since a click, reset nearby to false and nearbyCounter to 0 
        if (nearbyCount > (rate * .02)):
            nearby = False 
            nearbyCount = 0

        # if nearby a click then increment the clickCounter
        if (nearby):
            nearbyCount += 1

        # increment general counter
        counter += 1

    print(clickStartsSeconds) # test
    
    # DO THIS ONLY FOR NEUTRINO FILES
    #clickStartsSeconds = [0]
    #for i in wavArr:
        #if (i > clickStartsSeconds[0]):
            #clickStartsSeconds[0] = i
    
    # instantiate arrays for 1d and 2d CNNS
    fullX1d = np.array([])
    fullY1d = np.array([[0]])
    fullX2d = np.array([])
    fullY2d = np.array([[0]])
    
    # set spectrogram dimensions
    spectrum_timesteps = 192
    spectrum_frequencies = 129
    
    # construct spectrogram from when click occurs to .3 seconds after and append to time-series arrays
    imagePaths = []
    for j in range(len(clickStartsSeconds)):
        
        beginning = clickStartsSeconds[j]
        end = clickStartsSeconds[j] + .3
        
        # constructing spectrogram
        save_fn = spectrogram_folder_path + fn + "Spectrogram" + str(j) + ".png"
        print("Beginning: ", beginning, " End: ", end)
        spectrum = make_spectrogram(full_fn, beginning, end, save_fn)
        spectrum = spectrum.transpose()
        imagePaths.append(save_fn)
        
        # appending to arrays
        timesteps1d = np.array([])
        for k in range(j, j + int(.3 * rate)):
            timesteps1d = np.append(timesteps1d, np.array([wavArr[k]]), axis = 0)
        #np.savetxt(array_folder_path_1d, timesteps1d)
        #np.savetxt(array_folder_path_2d, spectrum)
        fullX1d = np.append(fullX1d, timesteps1d, axis = 0)
        fullX2d = np.append(fullX2d, spectrum)
        fullY1d = np.append(fullY1d, [[0]], axis = 0)
        fullY2d = np.append(fullY2d, [[0]], axis = 0)
        print("#", (j + 1), " out of ", len(clickStartsSeconds)) #TEST
    
    # reformat arrays
    fullX1d.resize(len(clickStartsSeconds), int(.3 * rate), 1)
    fullX2d.resize(len(clickStartsSeconds), spectrum_timesteps, spectrum_frequencies)

    # return all arrays
    return imagePaths, fullX1d, fullY1d[1:], fullX2d, fullY2d[1:]

In [16]:
# testing function on very small dataset

_, fullX1d, fullyY1d, fullX2d, fullyY2d = make_all_spectrograms("C:/Users/nssaf/Neutrino Project/data/clicks/", "Part 1", "C:/Users/nssaf/Neutrino Project/data/spectrograms/Wav 1/", "C:/Users/nssaf/Neutrino Project/data/spectrograms/1d arrays", "C:/Users/nssaf/Neutrino Project/data/spectrograms/2d arrays")

TypeError: make_all_spectrograms() takes 3 positional arguments but 5 were given

In [26]:
# making sure data is right

print(fullX1d.shape, fullyY1d.shape, fullX2d.shape, fullyY2d.shape)


(158, 43200, 1) (158, 1) (158, 192, 129) (158, 1)


In [20]:
# generate wav for all files

# clear former arrays
#fullX1d = np.array([])
#fullX1d.resize(0,43200,1)
#fullY1d = np.array([])
#fullX2d = np.array([])
#fullX2d.resize(0,192,129)
#fullY2d = np.array([])

# the number of wav files analyzed (up to x = 9)
x = 6

# for each wav file (represented by folder)
for i in range(4, x + 1):
    wav = "Wav " + str(i)
    print("\n\n\n\n", wav, "\n\n\n\n")
    # for each part of wav file (which is itself a wav file)
    for j in range(6, 9): # make sure to change 3 back to 1 after wav 4
        part = "Part " + str(j)
        print("\n\n\n\n", part, "\n\n\n\n")
        _, partX1d, partY1d, partX2d, partY2d = make_all_spectrograms("C:/Users/nssaf/Neutrino Project/data/clicks/" + wav + "/", part, "C:/Users/nssaf/Neutrino Project/data/spectrograms/" + wav + "/")
        # print dimensions (TEST)
        print(partX1d.shape, partX2d.shape) #TEST
        print(fullX1d.shape, fullX2d.shape) #TEST
        fullX1d = np.vstack((fullX1d, partX1d))
        #fullY1d = np.vstack((fullY1d, partY1d))
        fullX2d = np.vstack((fullX2d, partX2d))
        #fullY2d = np.vstack((fullY2d, partY2d))
        





 Wav 4 








 Part 6 






FileNotFoundError: [Errno 2] No such file or directory: 'C:/Users/nssaf/Neutrino Project/data/clicks/Wav 4/Part 6'

In [1]:
# parts done: all of wav's 1-4 and wav 5 part 3-5
print(fullX1d.shape, fullX2d.shape)
np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/Through_Wav4_and_more_1d", fullX1d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/Through_Wav4_and_more_2d", fullX2d)

NameError: name 'fullX1d' is not defined

In [25]:
# generate datset for all neutrinos (make sure to change in the code for neutrinos)
import glob, os

# clear former arrays
neutrinoX1d = np.array([])
neutrinoX1d.resize(0,43200,1)
neutrinoX2d = np.array([])
neutrinoX2d.resize(0,192,129)

dir_path = "C:/Users/nssaf/Neutrino Project/data/neutrino_clicks/"
spec_path = "C:/Users/nssaf/Neutrino Project/data/spectrograms/neutrino_spectrograms/"

os.chdir(dir_path)
counter = 0
# 1190 total
for file in glob.glob("*.wav"):
    _, partX1d, partY1d, partX2d, partY2d = make_all_spectrograms(dir_path, file, spec_path)   
    neutrinoX1d = np.vstack((neutrinoX1d, partX1d))
    neutrinoX2d = np.vstack((neutrinoX2d, partX2d))    
    counter = counter + 1
    print(counter, "/1190", "\n\n\n")

Average:  652.8533725738525 
Standard Deviation:  67.06416584682124 
Rate:  144000
(1048576,)
0
Noise:  652.1077461077978
Threshold  2934.48485748509
[]
Beginning:  912.0  End:  912.3


C:\Users\nssaf\Miniconda3\lib\site-packages\ipykernel_launcher.py:74: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
C:\Users\nssaf\Miniconda3\lib\site-packages\matplotlib\mlab.py:1246: UserWarning: Only one segment is calculated since parameter NFFT (=1024) >= signal length (=0).
  "(=%d) >= signal length (=%d)." % (NFFT, len(x)))
C:\Users\nssaf\Miniconda3\lib\site-packages\matplotlib\axes\_axes.py:7609: RuntimeWarning: divide by zero encountered in log10
  Z = 10. * np.log10(spec)
C:\Users\nssaf\Miniconda3\lib\site-packages\scipy\signal\spectral.py:1970: UserWarning: nperseg = 256 is greater than input length  = 0, using nperseg = 0
  .format(nperseg, input_length))
C:\Users\nssaf\Miniconda3\lib\site-packages\matplotlib\image.py:395: UserWarning: Warning: converting a masked element to nan.
  dv = (np.float64(self.norm.vmax) -
C:\Users\nssaf\Miniconda3\lib\site-packages\matplotlib\image.py:396: Use

# 1  out of  1
1 /1190 



Average:  882.3205699920654 
Standard Deviation:  60.11468213477549 
Rate:  144000
(1048576,)
0
0
Noise:  883.0234616002231
Threshold  3973.605577201004
[]
Beginning:  1224.0  End:  1224.3
# 1  out of  1
2 /1190 



Average:  361.75986671447754 
Standard Deviation:  236.09262847516644 
Rate:  144000
(1048576,)
0
Noise:  370.127094489851
Threshold  1665.5719252043295
[]
Beginning:  1208.0  End:  1208.3
# 1  out of  1
3 /1190 



Average:  322.77804470062256 
Standard Deviation:  318.54927384264204 
Rate:  144000
(1048576,)
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0

Noise:  70.76405319557402
Threshold  318.4382393800831
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.3859722

# 1  out of  1
14 /1190 



Average:  559.0881681442261 
Standard Deviation:  365.56337537938447 
Rate:  144000
(1048576,)
0
Noise:  560.2213938290699
Threshold  2520.9962722308146
[]
Beginning:  1703.0  End:  1703.3
# 1  out of  1
15 /1190 



Average:  24.786110877990723 
Standard Deviation:  82.47820937569865 
Rate:  144000
(1048576,)
0
Noise:  24.487908527789322
Threshold  110.19558837505195
[0.029416666666666667, 0.0729236111111111, 0.09685416666666667, 0.1809513888888889, 0.264125, 0.3275972222222222, 0.38959027777777777, 0.4205138888888889, 0.44824305555555555, 0.50225, 0.5936319444444444, 0.6185972222222222, 0.709875, 0.7756041666666667, 0.8590347222222222, 0.9400416666666667, 1.031638888888889, 1.1093194444444445, 1.1633819444444444, 1.2443194444444445, 1.3365486111111111, 1.3736180555555555, 1.4675138888888888, 1.5807708333333332, 1.6505902777777777, 1.7276875, 1.8033055555555555, 1.867625, 1.9381805555555556, 2.012770833333333, 2.071034722222222, 2.146375, 2.2527777777777778

...

Noise:  70.75625180129568
Threshold  318.40313310583053
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.385972

Noise:  70.75544110849359
Threshold  318.39948498822116
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.385972

Noise:  70.75389111423914
Threshold  318.39251001407615
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.385972

Noise:  70.76335222393955
Threshold  318.435085007728
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.38597222

Noise:  70.7633671771158
Threshold  318.4351522970211
[0.03847222222222222, 0.15484027777777779, 0.18695138888888888, 0.26927083333333335, 0.2932152777777778, 0.3844375, 0.5355694444444444, 0.6027569444444445, 0.9042013888888889, 0.941375, 0.9861597222222223, 1.019611111111111, 1.1219444444444444, 1.2370625, 1.3616944444444445, 1.4000972222222223, 1.5082291666666667, 1.543611111111111, 1.6924444444444444, 1.7859652777777777, 1.8144097222222222, 1.9181388888888888, 1.997451388888889, 2.0336666666666665, 2.1104583333333333, 2.2607430555555554, 2.3281319444444444, 2.4767847222222223, 2.57225, 2.6398055555555557, 2.7419861111111112, 2.8664722222222223, 2.951625, 3.0277777777777777, 3.0701597222222223, 3.110451388888889, 3.1416458333333335, 3.176409722222222, 3.263354166666667, 3.2953680555555556, 3.3354166666666667, 3.4761736111111112, 3.632715277777778, 3.6801180555555555, 3.8340625, 3.875763888888889, 3.9411597222222223, 4.047583333333334, 4.160791666666666, 4.263138888888889, 4.38597222

In [27]:
# save neutrino arrays

print(neutrinoX1d.shape, neutrinoX2d.shape)
np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/neutrinoX1d", neutrinoX1d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/neutrinoX2d", neutrinoX2d)

(1190, 43200, 1) (1190, 192, 129)


In [32]:
# combine neutrino and other neutrino arrays

fullX1d = np.load("C:/Users/nssaf/Neutrino Project/data/1d arrays/Through_Wav4_and_more_1d.npy")
fullX2d = np.load("C:/Users/nssaf/Neutrino Project/data/2d arrays/Through_Wav4_and_more_2d.npy")
print(fullX1d.shape, fullX2d.shape)
fullX1d = np.vstack((fullX1d, neutrinoX1d))
fullX2d = np.vstack((fullX2d, neutrinoX2d))
print(fullX1d.shape, fullX2d.shape)

(5002, 43200, 1) (5002, 192, 129)


In [44]:
# create y arrays 

fullY1d = np.vstack((np.zeros((3812, 1)), np.ones((1190, 1))))
fullY2d = np.vstack((np.zeros((3812, 1)), np.ones((1190, 1))))

In [45]:
# shuffle datsets

indices = np.arange(fullX1d.shape[0])
np.random.shuffle(indices)
fullX1d = fullX1d[indices]
fullX2d = fullX2d[indices]
fullY1d = fullY1d[indices]
fullY2d = fullY2d[indices]

In [47]:
# Reapportion training and testing sets

training_samples = int(fullX1d.shape[0] * .75)

# seperate training and testing arrays for 1d CNN
trainX1d = fullX1d[0:training_samples]
testX1d = fullX1d[training_samples:]
trainY1d = fullY1d[0:training_samples]
testY1d = fullY1d[training_samples:]

# seperate training and testing arrays for 2d CNN
trainX2d = fullX2d[0:training_samples]
testX2d = fullX2d[training_samples:]
trainY2d = fullY2d[0:training_samples]
testY2d = fullY2d[training_samples:]

In [49]:
# save datasets

np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/trainX1d", trainX1d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/testX1d", testX1d)
np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/trainY1d", trainY1d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/testY1d", testY1d)
np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/trainX2d", trainX2d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/testX2d", testX2d)
np.save("C:/Users/nssaf/Neutrino Project/data/1d arrays/trainY2d", trainY1d)
np.save("C:/Users/nssaf/Neutrino Project/data/2d arrays/testY2d", testY1d)